

# 📘 Stata Lecture Notes – Preparing for Lab 3

**Session Length**: \~4 hours
**Goal**: Students should confidently use `if/else`, create binary variables, write simple `programs`, loop over variable lists, and export regression tables.

---

## 🔹 1. Conditional Logic + Chi-Square

> 💡 *Stata can be taught to speak in complete English sentences — when you know how to control the logic.*

**Concepts Covered:**

* `tabulate var1 var2, chi2`
* `scalar`, `return list`
* `display`, `if`, `else`

### Example:

```stata
use transplants.dta, clear

tabulate rec_work gender, chi2

scalar p = r(p)

if p < 0.05 {
    display "Question 1: Working for income is associated with gender, p = " %5.3f p
}
else {
    display "Question 1: Working for income is NOT associated with gender, p = " %5.3f p
}
```

> ✅ **Skills Gained**: How to retrieve and use the p-value from a test using `scalar` and `if/else`.

---

## 🔹 2. Creating Clean Binary Variables

> 🧠 *Binary variables are the currency of logistic regression. You must be able to define your own currency.*

### Goal: Translate real-world conditions into clean 0/1 variables

```stata
gen hypertensive = (dx == 4)

gen college = ///
    inlist(educ, 4, 5, 6)  // any college, associates, bachelors, grad

gen male = (gender == 1)   // assuming 1=male, 2=female
```

> ✳️ Tip: Use `label define` and `label values` to keep your binary variables readable.

---

## 🔹 3. Logistic Regression and Interpreting Odds Ratios

```stata
logistic hypertensive age bmi college male
```

Then get readable odds ratios:

```stata
estimates store model1
esttab model1, eform
```

---

## 🔁 4. Writing a `program` to Display Odds Ratios in a Clean Format

> 🔄 *You don’t want to copy/paste regression output. Make Stata do it for you.*

### `table_loop` — Basic Loop Over Fixed Variables

```stata
program define table_loop
    foreach var in age bmi college male {
        quietly logistic hypertensive `var'
        local or = exp(_b[`var'])
        local lb = exp(_b[`var'] - 1.96 * _se[`var'])
        local ub = exp(_b[`var'] + 1.96 * _se[`var'])
        display "`var'" _col(15) %4.2f `or' " (" %4.2f `lb' " - " %4.2f `ub' ")"
    }
end

table_loop
```

> ✅ **Skills Gained**: Using coefficient and standard error to build a confidence interval manually.

---

## 🧰 5. Generalizing the Program with `syntax varlist`

> 🔧 *Now that they’ve seen it hardcoded, time to teach them how to generalize it with `syntax varlist`.*

### `table_varlist` – Flexible Version

```stata
program define table_varlist
    syntax varlist
    display "Regression table (Question 3)"
    foreach var of varlist `varlist' {
        quietly logistic hypertensive `var'
        local or = exp(_b[`var'])
        local lb = exp(_b[`var'] - 1.96 * _se[`var'])
        local ub = exp(_b[`var'] + 1.96 * _se[`var'])
        display "`var'" _col(15) %4.2f `or' " (" %4.2f `lb' " - " %4.2f `ub' ")"
    }
end

table_varlist age bmi college male
```

---

## 📊 6. Percentiles, Macros, and Variable Creation

> 📈 *How do you make a variable that depends on the 75th percentile of another?*

```stata
summarize rec_hgt_cm, detail
scalar p75 = r(p75)
gen tall = (rec_hgt_cm >= p75)
label variable tall "Height ≥ 75th percentile"
```

Other variables:

```stata
gen white = (race == 1) // assuming 1 = white
gen age_10y = age / 10
label variable age_10y "Age (per 10y)"
```

---

## 📤 7. Exporting a Clean Regression Table to Excel

> 📤 *Professional tables come from `putexcel`.*

```stata
logistic tall age_10y rec_wgt_kg gender white

putexcel set lab3_output.xlsx, replace
putexcel A1 = ("Variable") B1 = ("OR (95% CI)")

foreach var in age_10y rec_wgt_kg gender white {
    local or = exp(_b[`var'])
    local lb = exp(_b[`var'] - 1.96 * _se[`var'])
    local ub = exp(_b[`var'] + 1.96 * _se[`var'])
    local ci = string(`or', "%4.2f") + " (" + ///
                string(`lb', "%4.2f") + "-" + ///
                string(`ub', "%4.2f") + ")"
    putexcel A`=_n+1' = "`var'" B`=_n+1' = "`ci'"
}
```

---

## 🧠 End of Lecture: Recap + Stretch

**By now, they can:**

* Use conditional logic to control output
* Define 0/1 variables cleanly
* Run logistic models and interpret ORs
* Write flexible `program`s that loop
* Export clean tables to Excel

> 🧪 **Stretch challenge (optional)**: Try making `table_varlist` also accept the outcome variable as a parameter.

 